В этом ноутбуке мы попытаемся прогнозировать данные по транзакциям с использованием библиотеки пророк

Загрузим библиотеки и данные

In [1]:
# conda create -n myenv38 python=3.8
# conda activate myenv38
# conda install -c conda-forge fbprophet
%pip install prophet

     ---------------------------------------- 12.1/12.1 MB 7.2 MB/s eta 0:00:00
     -------------------------------------- 986.3/986.3 kB 3.7 MB/s eta 0:00:00
     -------------------------------------- 181.3/181.3 kB 3.6 MB/s eta 0:00:00
     ---------------------------------------- 78.4/78.4 kB 1.5 MB/s eta 0:00:00
     ---------------------------------------- 47.9/47.9 kB 1.2 MB/s eta 0:00:00
  Using cached matplotlib-3.5.3-cp38-cp38-win_amd64.whl (7.2 MB)
     ---------------------------------------- 80.7/80.7 kB 2.2 MB/s eta 0:00:00
     ---------------------------------------- 5.4/5.4 MB 6.7 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
     ---------------------------------------- 1.4/1.4 MB 5.0 MB/s eta 0:00:00
  Using cached cycler-0.11.0-py3-none-any.whl (6.4 kB)
     -------------------------------------- 956.5/956.5 kB 3.6 MB/s eta 0:00:00

     -------------------------------------- 55.4/55.4 kB 361.

In [2]:
# Load libraries
import numpy as np
RANDOM_SEED = 42
np.random.seed(RANDOM_SEED)
import pandas as pd
pd.set_option('display.max_rows', 10)
pd.set_option('display.max_columns', 70)
import plotly.offline as py
import plotly.graph_objs as go
py.init_notebook_mode()

# from fbprophet import Prophet
from prophet import Prophet

DIR="..\\..\\chunk\\15\\"
%time df_transactions = pd.read_csv(f'{DIR}transactions.csv')
%time df_holidays_events = pd.read_csv(f'{DIR}holidays_events.csv')

print('Data and libraries are loaded.')

CPU times: total: 31.2 ms
Wall time: 225 ms
CPU times: total: 0 ns
Wall time: 29 ms
Data and libraries are loaded.


In [3]:
#conda install fbprophet

In [3]:
df_transactions

date  store_nbr  transactions
0      2013-01-01         25           770
1      2013-01-02          1          2111
2      2013-01-02          2          2358
3      2013-01-02          3          3487
4      2013-01-02          4          1922
...           ...        ...           ...
83483  2017-08-15         50          2804
83484  2017-08-15         51          1573
83485  2017-08-15         52          2255
83486  2017-08-15         53           932
83487  2017-08-15         54           802

[83488 rows x 3 columns]

Если мы посмотрим на данные транзакций, транзакции сгруппированы по номерам магазинов. Сейчас мы упростим это и сгруппируем их по дате. 

In [4]:
transactions = df_transactions.groupby('date')['transactions'].sum()
py.iplot([go.Scatter(
    x=transactions.index,
    y=transactions
)])

Хорошо заметно влияние сезонности и праздников на общий объем транзакций.

Теперь давайте попробуем библиотеку пророк и посмотрим, насколько хорошо она предсказывает. Но перед этим мы должны подготовить данные. Согласно документации:

> Prophet следует API модели sklearn. Мы создаем экземпляр класса Prophet, а затем вызываем его методы соответствия и прогнозирования.
> Входными данными для Prophet всегда является фрейм данных с двумя столбцами: ** ds ** и ** y **. Столбец ds (отметка даты) должен содержать дату или дату и время (это нормально). Столбец ** y ** должен быть числовым и представлять измерение, которое мы хотим спрогнозировать.

In [5]:
transactions = pd.DataFrame(transactions).reset_index()
transactions.columns = ['ds', 'y']
transactions

ds      y
0     2013-01-01    770
1     2013-01-02  93215
2     2013-01-03  78504
3     2013-01-04  78494
4     2013-01-05  93573
...          ...    ...
1677  2017-08-11  89551
1678  2017-08-12  89927
1679  2017-08-13  85993
1680  2017-08-14  85448
1681  2017-08-15  86561

[1682 rows x 2 columns]

In [6]:
m = Prophet()
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)
forecast

19:17:17 - cmdstanpy - INFO - Chain [1] start processing
19:17:17 - cmdstanpy - INFO - Chain [1] done processing


ds         trend    yhat_lower     yhat_upper   trend_lower  \
0    2013-01-01  77977.407302  76390.517607   96174.836758  77977.407302   
1    2013-01-02  77987.191310  74541.446963   95543.742603  77987.191310   
2    2013-01-03  77996.975318  68917.600772   89182.392435  77996.975318   
3    2013-01-04  78006.759326  72776.826762   93327.459824  78006.759326   
4    2013-01-05  78016.543333  85149.428524  106516.799539  78016.543333   
...         ...           ...           ...            ...           ...   
2042 2018-08-11  97110.881093  96625.651891  116836.357819  96179.103873   
2043 2018-08-12  97127.402534  91179.943177  111531.955417  96190.628179   
2044 2018-08-13  97143.923975  80906.228126  102110.355271  96202.152486   
2045 2018-08-14  97160.445416  78885.196574   99289.128223  96213.676793   
2046 2018-08-15  97176.966857  81084.540736  101094.862292  96225.201099   

       trend_upper  additive_terms  additive_terms_lower  \
0     77977.407302     8037.533032           8037.533032   
1     77987.191310     7130.195483           7130.195483   
2     77996.975318     1619.097437           1619.097437   
3     78006.759326     5201.728981           5201.728981   
4     78016.543333    17877.080227          17877.080227   
...            ...             ...                   ...   
2042  98178.978021     9938.973170           9938.973170   
2043  98200.406164     4538.261288           4538.261288   
2044  98222.650523    -6005.205981          -6005.205981   
2045  98243.165042    -7740.796626          -7740.796626   
2046  98263.132356    -6524.594070          -6524.594070   

      additive_terms_upper        weekly  weekly_lower  weekly_upper  \
0              8037.533032  -4840.497932  -4840.497932  -4840.497932   
1              7130.195483  -3740.907230  -3740.907230  -3740.907230   
2              1619.097437  -7236.397130  -7236.397130  -7236.397130   
3              5201.728981  -1661.305058  -1661.305058  -1661.305058   
4             17877.080227  12952.805354  12952.805354  12952.805354   
...                    ...           ...           ...           ...   
2042           9938.973170  12952.805354  12952.805354  12952.805354   
2043           4538.261288   7553.715132   7553.715132   7553.715132   
2044          -6005.205981  -3027.413136  -3027.413136  -3027.413136   
2045          -7740.796626  -4840.497932  -4840.497932  -4840.497932   
2046          -6524.594070  -3740.907230  -3740.907230  -3740.907230   

            yearly  yearly_lower  yearly_upper  multiplicative_terms  \
0     12878.030964  12878.030964  12878.030964                   0.0   
1     10871.102713  10871.102713  10871.102713                   0.0   
2      8855.494567   8855.494567   8855.494567                   0.0   
3      6863.034039   6863.034039   6863.034039                   0.0   
4      4924.274873   4924.274873   4924.274873                   0.0   
...            ...           ...           ...                   ...   
2042  -3013.832183  -3013.832183  -3013.832183                   0.0   
2043  -3015.453844  -3015.453844  -3015.453844                   0.0   
2044  -2977.792845  -2977.792845  -2977.792845                   0.0   
2045  -2900.298693  -2900.298693  -2900.298693                   0.0   
2046  -2783.686840  -2783.686840  -2783.686840                   0.0   

      multiplicative_terms_lower  multiplicative_terms_upper           yhat  
0                            0.0                         0.0   86014.940334  
1                            0.0                         0.0   85117.386793  
2                            0.0                         0.0   79616.072755  
3                            0.0                         0.0   83208.488307  
4                            0.0                         0.0   95893.623560  
...                          ...                         ...            ...  
2042                         0.0                         0.0  107049.854263  
2043                     

In [7]:
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

In [8]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )

RMSE: 7904.159810


Как видно на графике выше, прогноз довольно хороший и согласуется с взлетами и падениями данных. Вы можете увеличить график, выбрав область масштабирования с помощью мыши.

Но тенденция довольно жесткая, она не учитывает под-тренды середины года. В первой половине года тенденция нарастает, а затем немного замедляется. Сделаем тренд немного гибким. Если тренд является переобученным (слишком большая гибкость) или недостаточными (недостаточная гибкость), вы можете отрегулировать силу разреженности перед использованием входного аргумента ** changepoint_prior_scale **. По умолчанию этот параметр установлен на 0,05. Его увеличение сделает тренд более гибким. (https://facebook.github.io/prophet/docs/trend_changepoints.html)

In [9]:
m = Prophet(changepoint_prior_scale=2.5)
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)

19:17:41 - cmdstanpy - INFO - Chain [1] start processing
19:17:42 - cmdstanpy - INFO - Chain [1] done processing


In [10]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

RMSE: 7859.496207


Теперь добавим в модель больше сезонности. Как мы видим, Пророк рассчитывает еженедельную и годовую сезонность. Нам не нужна ежедневная сезонность, потому что у нас нет внутридневных данных для этого случая. Достаточно просто добавить ежемесячную сезонность.

In [11]:
m = Prophet(changepoint_prior_scale=2.5)
m.add_seasonality(name='monthly', period=30.5, fourier_order=5)
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)

19:17:58 - cmdstanpy - INFO - Chain [1] start processing
19:17:59 - cmdstanpy - INFO - Chain [1] done processing


In [12]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

RMSE: 7683.106689


Пришло время добавить в нашу модель влияние праздников. Сначала нам нужно настроить формат данных. Пророку нужны два столбца (праздник и ds) и строка для каждого наступления праздника. Так же можно включить столбцы lower_window и upper_window, которые продлевают праздничные дни до дней «[lower_window, upper_window]» вокруг даты. 

In [13]:
df_holidays_events

date        type    locale locale_name  \
0    2012-03-02     Holiday     Local       Manta   
1    2012-04-01     Holiday  Regional    Cotopaxi   
2    2012-04-12     Holiday     Local      Cuenca   
3    2012-04-14     Holiday     Local    Libertad   
4    2012-04-21     Holiday     Local    Riobamba   
..          ...         ...       ...         ...   
345  2017-12-22  Additional  National     Ecuador   
346  2017-12-23  Additional  National     Ecuador   
347  2017-12-24  Additional  National     Ecuador   
348  2017-12-25     Holiday  National     Ecuador   
349  2017-12-26  Additional  National     Ecuador   

                       description  transferred  
0               Fundacion de Manta        False  
1    Provincializacion de Cotopaxi        False  
2              Fundacion de Cuenca        False  
3        Cantonizacion de Libertad        False  
4        Cantonizacion de Riobamba        False  
..                             ...          ...  
345                      Navidad-3        False  
346                      Navidad-2        False  
347                      Navidad-1        False  
348                        Navidad        False  
349                      Navidad+1        False  

[350 rows x 6 columns]

In [14]:
holidays = df_holidays_events[df_holidays_events['transferred'] == False][['description', 'date']]
holidays.columns = ['holiday', 'ds']
#holidays['lower_window'] = 0
#holidays['upper_window'] = 0
holidays

holiday          ds
0               Fundacion de Manta  2012-03-02
1    Provincializacion de Cotopaxi  2012-04-01
2              Fundacion de Cuenca  2012-04-12
3        Cantonizacion de Libertad  2012-04-14
4        Cantonizacion de Riobamba  2012-04-21
..                             ...         ...
345                      Navidad-3  2017-12-22
346                      Navidad-2  2017-12-23
347                      Navidad-1  2017-12-24
348                        Navidad  2017-12-25
349                      Navidad+1  2017-12-26

[338 rows x 2 columns]

In [15]:
m = Prophet(changepoint_prior_scale=2.5, holidays=holidays)
m.add_seasonality(name='monthly', period=30.5, fourier_order=5)
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)

19:18:21 - cmdstanpy - INFO - Chain [1] start processing
19:18:24 - cmdstanpy - INFO - Chain [1] done processing


In [16]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

RMSE: 4929.982700


Нам удалось спрогнозировать всплески на новогодний период. Модель не смогла уловить резкий скачок вниз на 4 января 2016 года, поэтому она не смогла успешно спрогнозировать 1 января 2017 года. 
Это объясняется тем, что 4 января 2016 года не было выходных. Но модель хорошо предсказывает продажи на 24 декабря. А также прогнозируемый период после 15 августа 2017 года выглядит неплохо.


Prophet - это довольно простая в использовании библиотека для прогнозирования данных временных рядов, которая использует для этого только предыдущие данные и праздники. Есть другие функции и параметры, такие как прогнозы насыщения, интервалы неопределенности и т. Д., Которые мы здесь не рассматривали. Вы можете прочитать больше в статье https://peerj.com/preprints/3190.pdf.